# CPE210 vs CPE510 $P_\mathrm{rx}$

The goal is to choose the one with a better range using the datasheet.

The datasheet is available on [this page](https://www.tp-link.com/us/support/download/cpe510/). For the calculations, I used [this version of the datasheet](https://static.tp-link.com/upload/product-overview/2023/202308/20230828/CPE%20series-Datasheet.pdf).

Relevant data:
- Frequency on PDF page 5
- Transmit power on PDF page 5 
- antenna gain on PDF page 4

Using these, we can calculate the receive power $P_\mathrm{rx}$.

In [1]:
CPE210_F = 2.44e6  # Hz (took the middle frequency)
CPE510_F = 5.155e6  # Hz
CPE210_P_TX = 25  # dB
CPE510_P_TX = 26  # dB
CPE210_G_TX = 9  # dBi
CPE510_G_TX = 13  # dBi
DISTANCE = 20  # km

In [2]:
from dataclasses import dataclass
from sympy import log, symbols, sympify
import pandas as pd  # For tabular viewing of results

I used the symbolic math library, SymPy, to view the formulas more clearly.

Let us define FSPL first:

In [3]:
def fspl(d, f):
    return 20 * log(d, 10) + 20 * log(f, 10) - 147.55

d, f = symbols("d f")
# d and f will be math symbols instead of ordinary variables

fspl(d, f)

20*log(d)/log(10) + 20*log(f)/log(10) - 147.55

Put the properties into a class and create devices with their properties.

In [4]:
@dataclass
class Device:
    f: float
    tx_power: float
    gain: float

    def p_rx(self, d):
        return self.tx_power + self.gain - fspl(d, self.f) + self.gain


cpe210 = Device(CPE210_F, CPE210_P_TX, CPE210_G_TX)
cpe510 = Device(CPE510_F, CPE510_P_TX, CPE510_G_TX)

Losses:

In [5]:
display(cpe210.p_rx(d))
display(cpe510.p_rx(d))

-20*log(d)/log(10) - 294.150171945388/log(10) + 190.55

-20*log(d)/log(10) - 309.109553508664/log(10) + 199.55

Losses at 20, 15 and 5 km:

In [6]:
data = {
    ("", "Device"): ["CPE210", "CPE510"],  # Empty first level for consistency
    ("P_rx (dB)", "5 km"): [cpe210.p_rx(5e3).evalf(n=3), cpe510.p_rx(5e3).evalf(n=3)],
    ("P_rx (dB)", "15 km"): [cpe210.p_rx(15e3).evalf(n=3), cpe510.p_rx(15e3).evalf(n=3)],
    ("P_rx (dB)", "20 km"): [cpe210.p_rx(20e3).evalf(n=3), cpe510.p_rx(20e3).evalf(n=3)],
}

df = pd.DataFrame(data)
display(df)

P_rx (dB)              
   Device      5 km  15 km  20 km
0  CPE210     -11.2  -20.7  -23.2
1  CPE510     -8.67  -18.2  -20.7

CPE510 has less loss, so we should go for CPE510.

Other aspects that could speak for 5 GHz, even 2.4 GHz can penetrate obstacles easily and may have a better range in indoor environments:

- other wireless technologies are operating in the 2.4 GHz spectrum. This causes interference, and thus, the noise in the receiver will be higher.
- The Fresnel zone of 2.4 GHz is larger than the Fresnel zone of 5 GHz. This increases the probability of obstacles disturbing the LOS.
- According to the datasheet available on [this page](https://www.tp-link.com/us/support/download/cpe510/), CPE510 has about 5 dB less return loss on average for vertical polarization in the operating frequency range.
- the datasheet and claimed values are not precise enough 🙂
- more info [on this forum post](https://community.tp-link.com/en/business/forum/topic/750648)